# Homework : Vector Search

## Q1. Getting the embeddings model

In [105]:
import json
from sentence_transformers import SentenceTransformer, util

In [106]:
model = "sentence-transformers/multi-qa-distilbert-cos-v1"

In [107]:
embedding_model = SentenceTransformer(model)

In [108]:
user_question = "I just discovered the course. Can I still join it?"

In [109]:
encoded = embedding_model.encode(user_question)

In [130]:
first_value = round(encoded[0],3)
f"The first value of the resulting vector is {first_value}"

'The first value of the resulting vector is 0.07800000160932541'

In [111]:
import requests 

base_url = 'https://github.com/DataTalksClub/llm-zoomcamp/blob/main'
relative_url = '03-vector-search/eval/documents-with-ids.json'
docs_url = f'{base_url}/{relative_url}?raw=1'
docs_response = requests.get(docs_url)
documents = docs_response.json()

In [112]:
documents_trimmed=[]
for doc in documents:
    if doc['course'] == 'machine-learning-zoomcamp':
        documents_trimmed.append(doc)

In [113]:
len(documents_trimmed)

375

## Q2 Creating the embeddings

In [114]:
for docs in documents_trimmed:
    print(docs)

{'text': 'Machine Learning Zoomcamp FAQ\nThe purpose of this document is to capture frequently asked technical questions.\nWe did this for our data engineering course and it worked quite well. Check this document for inspiration on how to structure your questions and answers:\nData Engineering Zoomcamp FAQ\nIn the course GitHub repository there’s a link. Here it is: https://airtable.com/shryxwLd0COOEaqXo\nwork', 'section': 'General course-related questions', 'question': 'How do I sign up?', 'course': 'machine-learning-zoomcamp', 'id': '0227b872'}
{'text': 'The course videos are pre-recorded, you can start watching the course right now.\nWe will also occasionally have office hours - live sessions where we will answer your questions. The office hours sessions are recorded too.\nYou can see the office hours as well as the pre-recorded course videos in the course playlist on YouTube.', 'section': 'General course-related questions', 'question': 'Is it going to be live? When?', 'course': 'ma

In [115]:
embeddings = []

for docs in documents_trimmed:
    qa_text = f'{docs["question"]} {doc["text"]}'
    embedding = embedding_model.encode(qa_text)
    embeddings.append(embedding)

In [116]:
embeddings

[array([ 4.43900004e-02, -6.27251389e-03,  1.67786740e-02, -2.19876450e-02,
         9.28844586e-02,  5.25975749e-02,  5.77343022e-03,  1.88148580e-02,
         7.30139539e-02,  4.43461863e-03, -7.22151948e-04,  4.33124006e-02,
         5.51878847e-02,  2.67423894e-02, -5.28423972e-02,  2.99931858e-02,
        -2.13135071e-02, -5.41415764e-03,  1.33024324e-02,  2.73396410e-02,
         1.10568693e-02, -1.66124124e-02,  1.93539895e-02,  1.21758756e-04,
        -8.47344566e-03,  7.53414410e-04, -1.25102401e-02,  6.83525624e-03,
        -5.07206470e-02, -4.97601666e-02, -1.11672990e-02,  2.81651388e-03,
         1.57574341e-02, -2.79497169e-02,  4.20119939e-03, -2.24066824e-02,
        -3.92604731e-02,  3.74372564e-02, -1.04365463e-03, -7.65044466e-02,
         3.36016039e-03,  2.43088771e-02,  3.28683294e-04, -3.81189957e-02,
         2.03809869e-02, -3.42039531e-03, -4.60149422e-02, -2.44924482e-02,
         1.44408550e-02, -2.06875075e-02,  2.09152866e-02, -1.02701858e-02,
        -1.6

In [117]:
import numpy as np

In [118]:
X = np.array(embeddings)

In [119]:
X.shape

(375, 768)

## Q3 Search

In [125]:
encoded[0]

0.07822264

In [120]:
v=encoded

In [121]:
scores = X.dot(v)

In [122]:
scores.max()

0.40679222

In [123]:
np.max(scores)

0.40679222

### Vector Search 

In [126]:
class VectorSearchEngine():
    def __init__(self, documents, embeddings):
        self.documents = documents
        self.embeddings = embeddings

    def search(self, v_query, num_results=10):
        scores = self.embeddings.dot(v_query)
        idx = np.argsort(-scores)[:num_results]
        return [self.documents[i] for i in idx]

search_engine = VectorSearchEngine(documents=documents, embeddings=X)
search_engine.search(v, num_results=5)

[{'text': 'Yes! Every “Office Hours” will be recorded and available a few minutes after the live session is over; so you can view (or rewatch) whenever you want.',
  'section': 'General course-related questions',
  'question': 'Office Hours - I can’t attend the “Office hours” / workshop, will it be recorded?',
  'course': 'data-engineering-zoomcamp',
  'id': '9681be3b'},
 {'text': 'After you submit your homework it will be graded based on the amount of questions in a particular homework. You can see how many points you have right on the page of the homework up top. Additionally in the leaderboard you will find the sum of all points you’ve earned - points for Homeworks, FAQs and Learning in Public. If homework is clear, others work as follows: if you submit something to FAQ, you get one point, for each learning in a public link you get one point.\n(https://datatalks-club.slack.com/archives/C01FABYF2RG/p1706846846359379?thread_ts=1706825019.546229&cid=C01FABYF2RG)',
  'section': 'General

# Q4 Hit-rate for our search engine

In [127]:
import pandas as pd

base_url = 'https://github.com/DataTalksClub/llm-zoomcamp/blob/main'
relative_url = '03-vector-search/eval/ground-truth-data.csv'
ground_truth_url = f'{base_url}/{relative_url}?raw=1'

df_ground_truth = pd.read_csv(ground_truth_url)
df_ground_truth = df_ground_truth[df_ground_truth.course == 'machine-learning-zoomcamp']
ground_truth = df_ground_truth.to_dict(orient='records')

In [131]:
ground_truth


[{'question': 'Where can I sign up for the course?',
  'course': 'machine-learning-zoomcamp',
  'document': '0227b872'},
 {'question': 'Can you provide a link to sign up?',
  'course': 'machine-learning-zoomcamp',
  'document': '0227b872'},
 {'question': 'Is there an FAQ for this Machine Learning course?',
  'course': 'machine-learning-zoomcamp',
  'document': '0227b872'},
 {'question': 'Does this course have a GitHub repository for the sign-up link?',
  'course': 'machine-learning-zoomcamp',
  'document': '0227b872'},
 {'question': 'How can I structure my questions and answers for the course?',
  'course': 'machine-learning-zoomcamp',
  'document': '0227b872'},
 {'question': 'Are the course videos live or pre-recorded?',
  'course': 'machine-learning-zoomcamp',
  'document': '39fda9f0'},
 {'question': 'When can I start watching the course videos?',
  'course': 'machine-learning-zoomcamp',
  'document': '39fda9f0'},
 {'question': 'Are the live office hours sessions recorded?',
  'cours

In [132]:
def hit_rate(relevance_total):
    cnt = 0

    for line in relevance_total:
        if True in line:
            cnt = cnt + 1

    return cnt / len(relevance_total)

In [133]:
def evaluate(ground_truth, search_function):
    relevance_total = []

    for q in ground_truth:
        doc_id = q['document']
        results = search_function(q)
        relevance = [d['id'] == doc_id for d in results]
        relevance_total.append(relevance)

    return {
        'hit_rate': hit_rate(relevance_total),
    }

In [134]:
evaluate(ground_truth,search_engine.search())

TypeError: VectorSearchEngine.search() missing 1 required positional argument: 'v_query'